In [1]:
import pandas as pd
import yfinance as yf
import plotly.graph_objects as go

In [2]:
# Get S&P 500 companies with theirs tickers: less stable but faster method
wiki_url = "https://en.wikipedia.org/wiki/List_of_S&P_500_companies"
# identify the table in the HTML by its unique id
sp500 = pd.read_html(wiki_url, attrs={"id": "constituents"})[0]
sp500.sort_values("Symbol", inplace=True)

In [3]:
ticker_list = ["GOOG", "TSLA", "BF.B", "META", "AAPL"]
start = "1960-01-01"
end = pd.Timestamp.today()
interval = "1d"

In [4]:
def get_stocks_data(ticker_list, start, end, interval):
    stock_history_dict = {}
    stock_info = []
    for ticker in ticker_list:
        try:
            stock = yf.Ticker(ticker)
            stock.info["shortName"]
        except KeyError:
            stock = yf.Ticker(ticker.replace(".", "-"))
        stock_history = stock.history(start=start, end=end, interval=interval)
        stock_history_dict[ticker] = stock_history
        stock_info.append(stock.info["shortName"])
    return stock_history_dict, stock_info

In [5]:
stocks_data = get_stocks_data(ticker_list, start, end, interval)

In [6]:
def update_charts(state):
    state.stocks_data = get_stocks_data(
        state.ticker_list, state.start, state.end, state.interval
    )
    # Notify no data found:
    if len(state.stocks_data[0]) == 0:
        notify(
            state,
            "error",
            f"Error: No data found for {state.ticker} from {state.start} to {state.end}",
        )
    else:
        notify(state, "success", "Historical data has been updated")

In [7]:
def create_cards(ticker_list, stocks_data):
    # Dynamically calculate plotly subplot grid layout
    n_plots = len(stocks_data[1])
    rows_added = 2
    # Square root aims to create a balanced grid with roughly equal numbers of rows and columns:
    cols = 4 if n_plots < 16 else int(n_plots ** (1 / 2))
    # Round up by double negative of result from rounding down:
    rows = -(-n_plots // cols) + rows_added
    specs_grid = [[{} for _ in range(cols)] for _ in range(rows - rows_added)]
    specs_linechart_row = [None] * (cols - 1)
    specs_last_row = [None] * (cols)
    fig_sparkline = go.Figure().set_subplots(
        rows,
        cols,
        vertical_spacing=0.1,
        horizontal_spacing=0.1,
        specs=specs_grid
        + [[{"colspan": cols, "rowspan": rows_added}] + specs_linechart_row]
        + [specs_last_row],
    )
    fig_sparkline.update_layout(
        margin={"l": 100, "r": 10, "t": 60, "b": 10}, height=130 * rows
    )
    for i, ticker in enumerate(ticker_list):
        row = (i // cols) + 1  # round down to whole nearest number
        col = (i % cols) + 1  # division remainder
        fig_sparkline.add_trace(
            go.Scatter(
                x=stocks_data[0][ticker].index,
                y=stocks_data[0][ticker]["Close"],
                fill="tozeroy",
                line_color="red",
                fillcolor="pink",
                showlegend=False,
            ),
            row=row,
            col=col,
        )
        fig_sparkline.update_xaxes(showgrid=False, visible=False, row=row, col=col)
        fig_sparkline.update_yaxes(showgrid=False, visible=False, row=row, col=col)
        # Calculate delta for annotations:
        delta_percent = (
            stocks_data[0][ticker].iloc[-1]["Close"]
            / stocks_data[0][ticker].iloc[-2]["Close"]
        ) - 1
        delta_symbol = "▲" if delta_percent >= 0 else "▼"
        delta_color = "green" if delta_percent >= 0 else "red"
        # Insert annotations:
        fig_sparkline.add_annotation(
            text=f"{ticker}<br><span style='color:{delta_color}'>{delta_symbol} {abs(delta_percent):.2%}</span>",
            xref="x domain",  # Refer to the x-axis domain of the subplot
            yref="y domain",  # Refer to the y-axis domain of the subplot
            x=1,  # Position 100% from the left (almost right edge)
            y=1.6,  # Position 115% from the bottom (almost top edge)
            row=row,
            col=col,
            showarrow=False,
            align="right",
        )
        fig_sparkline.add_annotation(
            text=f"<b>{stocks_data[1][i]}</b><br><br><span style='color:grey'>Current Price</span><br><b>${stocks_data[0][ticker].iloc[-1]['Close']:.2f}</b>",
            xref="x domain",
            yref="y domain",
            x=-0.5,
            y=1.6,
            row=row,
            col=col,
            showarrow=False,
            align="left",
        )
        # Insert rounded-corner borders using SVG `path` syntax:
        x0, y0 = -0.5, -0.05
        x1, y1 = 1.02, 1.8
        radius = 0.07
        rounded_bottom_left = f" M {x0+radius}, {y0} Q {x0}, {y0} {x0}, {y0+radius}"
        rounded_top_left = f" L {x0}, {y1-radius} Q {x0}, {y1} {x0+radius}, {y1}"
        rounded_top_right = f" L {x1-radius}, {y1} Q {x1}, {y1} {x1}, {y1-radius}"
        rounded_bottom_right = f" L {x1}, {y0+radius} Q {x1}, {y0} {x1-radius}, {y0}Z"
        path = (
            rounded_bottom_left
            + rounded_top_left
            + rounded_top_right
            + rounded_bottom_right
        )
        fig_sparkline.add_shape(
            type="path",
            path=path,
            xref="x domain",
            yref="y domain",
            row=row,
            col=col,
            line={"color": "grey"},
        )
    # Create a separate line chart:
    for ticker in ticker_list:
        fig_sparkline.add_trace(
            go.Scatter(
                x=stocks_data[0][ticker].index,
                y=stocks_data[0][ticker]["Close"],
                name=ticker,
                showlegend=True,
            ),
            row=rows - rows_added + 1,
            col=1,
        )
    # Define a global range selector that will affect all subplots that share the x-axis by applying the range selector configuration to the layout of the figure: specifically to the x-axis
    fig_sparkline.update_layout(
        xaxis={
            "rangeselector": {
                "buttons": [
                    {
                        "label": "1 month",
                        "count": 1,
                        "step": "month",
                        "stepmode": "backward",
                    },
                    {
                        "label": "6 months",
                        "count": 6,
                        "step": "month",
                        "stepmode": "backward",
                    },
                    {"label": "YTD", "count": 1, "step": "year", "stepmode": "todate"},
                    {
                        "label": "1 year",
                        "count": 1,
                        "step": "year",
                        "stepmode": "backward",
                    },
                    {"step": "all"},
                ],
                "bgcolor": "rgba(0,0,0,0)",
                "activecolor": "gray",
                "bordercolor": "gray",
                "borderwidth": 1,
            }
        }
    )
    # matches="x" link the x-axes of all subplots hence all subplots will have their x-axis ranges updated synchronously
    fig_sparkline.update_xaxes(matches="x", rangeselector_x=0, rangeselector_y=1.1)
    return fig_sparkline

In [8]:
create_cards(ticker_list, stocks_data)

In [9]:
def create_line_chart(ticker_list, stocks_data):
    fig_line_chart = go.Figure()
    for ticker in ticker_list:
        fig_line_chart.add_trace(
            go.Scatter(
                x=stocks_data[0][ticker].index,
                y=stocks_data[0][ticker]["Close"],
                name=ticker,
                showlegend=True,
            )
        )
    fig_line_chart.update_xaxes(
        rangeselector={
            "buttons": [
                {
                    "label": "1 month",
                    "count": 1,
                    "step": "month",
                    "stepmode": "backward",
                },
                {
                    "label": "6 months",
                    "count": 6,
                    "step": "month",
                    "stepmode": "backward",
                },
                {"label": "YTD", "count": 1, "step": "year", "stepmode": "todate"},
                {"label": "1 year", "count": 1, "step": "year", "stepmode": "backward"},
                {"step": "all"},
            ],
            "bgcolor": "rgba(0,0,0,0)",
            "activecolor": "gray",
            "bordercolor": "gray",
            "borderwidth": 1,
        }
    )
    fig_line_chart.update_layout(
        title=f"Historical Price over the Period for: {', '.join(ticker_list)}"
    )
    return fig_line_chart

In [10]:
create_line_chart(ticker_list, stocks_data)

In [11]:
from taipy.gui import Gui, notify
import taipy.gui.builder as tgb

company_list = list(zip(sp500["Symbol"], sp500["Symbol"] + ": " + sp500["Security"]))
interval_list = [  # 1 minute is available but date range would be limited to 8 days
    ("1d", "1 day"),
    ("5d", "5 days"),
    ("1wk", "1 week"),
    ("1mo", "1 month"),
    ("3mo", "3 months"),
]
with tgb.Page() as page:
    with tgb.part("container"):
        with tgb.layout(columns="1 2", gap="30px", class_name="card"):
            with tgb.part():
                tgb.text("#### Selected **Period**", mode="md")
                tgb.text("**From:**", mode="md")
                tgb.date(
                    "{start}",
                    format="dd/MM/y",
                    on_change=update_charts,
                )
                tgb.text("**To:**", mode="md")
                tgb.date(
                    "{end}",
                    format="dd/MM/y",
                    on_change=update_charts,
                )
            with tgb.part():
                tgb.text("#### Selected **Ticker**", mode="md")
                tgb.text("Choose any tickers from the dropdown list below:", mode="md")
                tgb.selector(
                    value="{ticker_list}",
                    label="Companies",
                    dropdown=True,
                    multiple=True,
                    lov="{company_list}",  # search-in-place or search-within-dropdown
                    on_change=update_charts,
                    value_by_id=True,
                )
                tgb.text("Choose interval:", mode="md")
                tgb.toggle(
                    value="{interval}",
                    lov="{interval_list}",
                    on_change=update_charts,
                    value_by_id=True,
                )
        tgb.html("br")
        tgb.chart(figure="{create_cards(ticker_list,stocks_data)}")
        tgb.html("br")
        tgb.chart(
            figure="{create_line_chart(ticker_list, stocks_data)}",
        )

In [12]:
gui = Gui(page)
gui.run(dev_mode=True, watermark="")

[2025-01-16 19:46:11.545][Taipy][INFO] Running in 'single_client' mode in notebook environment
[2025-01-16 19:46:16.132][Taipy][INFO]  * Server starting on http://127.0.0.1:5000


c:\Users\maitp\anaconda3\envs\general\Lib\site-packages\gevent\hub.py:161: UserWarning:

libuv only supports millisecond timer resolution; all times less will be set to 1 ms



c:\Users\maitp\anaconda3\envs\general\Lib\site-packages\taipy\gui\utils\_evaluator.py:369: TaipyGuiWarning:

Exception raised evaluating create_cards(ticker_list,stocks_data):
'MHK'

c:\Users\maitp\anaconda3\envs\general\Lib\site-packages\taipy\gui\utils\_evaluator.py:369: TaipyGuiWarning:

Exception raised evaluating create_line_chart(ticker_list, stocks_data):
'MHK'

